In [2]:
import pandas as pd
import torch
from transformers import T5ForConditionalGeneration, T5Tokenizer, AdamW
from torch.utils.data import DataLoader, Dataset
from tqdm import tqdm
import time
import os

In [3]:
# загрузка датасета
file_path = './train.tsv'
train_df = pd.read_csv(file_path, sep='\t').drop('index', axis=1).fillna('')

In [4]:
# делаем шаблон для параллельного корпуса
df_paraphrase = pd.DataFrame(columns=['source_sentence', 'target_sentence'])

In [5]:
df_paraphrase

Empty DataFrame
Columns: [source_sentence, target_sentence]
Index: []

In [6]:
# Добавляем новую строку в df_paraphrase с исходным токсичным комментарием и текущим нейтральным комментарием
for _, row in train_df.iterrows():
    references = row[['neutral_comment1', 'neutral_comment2', 'neutral_comment3']].tolist()

    for reference in references:
        if len(reference) > 0:
            df_paraphrase = df_paraphrase.append({
                'source_sentence': row['toxic_comment'],
                'target_sentence': reference
            }, ignore_index=True)

<ipython-input-6-d9f305c9e9c9>:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_paraphrase = df_paraphrase.append({
<ipython-input-6-d9f305c9e9c9>:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_paraphrase = df_paraphrase.append({
<ipython-input-6-d9f305c9e9c9>:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_paraphrase = df_paraphrase.append({
<ipython-input-6-d9f305c9e9c9>:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_paraphrase = df_paraphrase.append({
<ipython-input-6-d9f305c9e9c9>:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
 

In [7]:
# Перемешиваем строки датафрейма случайным образом и сбрасываем индекс, чтобы получить новый порядковый индекс
df_paraphrase = df_paraphrase.sample(frac=1).reset_index(drop=True)

In [8]:
df_paraphrase.head()

source_sentence                                    target_sentence
0  .этих тварей постоянно хочется целовать и тиск...  Этих животных постоянно хочется целовать и тис...
1  она уже заебала &gt;&lt;Нах вообще было открыв...  Она уже надоела. Зачем вообще было открывать м...
2  Бля,да че так скучно то?Без молодежки нечего д...  Да почему так скучно-то? Без молодежи нечего д...
3            опять одни и те же нищеброды заскулили)  Опять одни и теже бедные деньгами люди заговорили
4  я вообще ничего не писала, а вот ты постоянно ...  Я вообще ничего не писала, а вот ты постоянно ...

In [9]:
%pip install sentencepiece

Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip is available: 23.2.1 -> 24.0
[notice] To update, run: python3 -m pip install --upgrade pip


In [9]:
# Определяем модель и токенизатор
backbone_model = 'cointegrated/rut5-base-paraphraser'
model = T5ForConditionalGeneration.from_pretrained(backbone_model)
tokenizer = T5Tokenizer.from_pretrained(backbone_model)

You are using the default legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thoroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565


In [ ]:
# Определяем класс для создания датасета, который будет использоваться для обучения модели
class ParaphraseDataset(Dataset):
    def __init__(self, source_sentences, target_sentences, tokenizer, max_source_length=128, max_target_length=128):
        self.source_sentences = source_sentences
        self.target_sentences = target_sentences
        self.tokenizer = tokenizer
        self.max_source_length = max_source_length
        self.max_target_length = max_target_length

    def __len__(self):
        return len(self.source_sentences)

    def __getitem__(self, idx):
        source_tokenized = self.tokenizer.encode_plus(self.source_sentences[idx], max_length=self.max_source_length, padding="max_length", return_tensors="pt", truncation=True)
        target_tokenized = self.tokenizer.encode_plus(self.target_sentences[idx], max_length=self.max_target_length, padding="max_length", return_tensors="pt", truncation=True)
        return {
            "source_ids": source_tokenized["input_ids"].flatten(),
            "source_mask": source_tokenized["attention_mask"].flatten(),
            "target_ids": target_tokenized["input_ids"].flatten(),
            "target_mask": target_tokenized["attention_mask"].flatten()

In [ ]:
# Получаем исходные и целевые предложения из датафрейма df_paraphrase
source_sentences = df_paraphrase['source_sentence']
target_sentences = df_paraphrase['target_sentence']

In [ ]:
# Создаем датасет с использованием исходных и целевых предложений и токенизатора
paraphrase_dataset = ParaphraseDataset(source_sentences, target_sentences, tokenizer)
# Создаем загрузчик данных 
paraphrase_dataloader = DataLoader(paraphrase_dataset, batch_size=6, shuffle=True)


In [ ]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

In [ ]:
num_epochs = 15

In [ ]:
model.train()

# определяем оптимизатор AdamW с заданной скоростью обучения
optimizer = AdamW(model.parameters(), lr=1e-5)

# количество эпох обучения
num_epochs = 15


In [ ]:
# Создание tqdm индикатора для эпох
epoch_iterator = tqdm(range(num_epochs), desc="Epoch")

In [ ]:
for epoch in range(num_epochs):
    # тут мы создаем индикатор tqdm для батчей с указанием номера эпохи
    batch_iterator = tqdm(paraphrase_dataloader, desc=f"Epoch {epoch + 1}", leave=False)

    # Проходим по каждому батчу
    for batch in batch_iterator:
        # Переносим данные на устройство (GPU, если доступен)
        input_ids = batch["source_ids"].to(device)
        attention_mask = batch["source_mask"].to(device)
        labels = batch["target_ids"].to(device)
        labels_attention_mask = batch["target_mask"].to(device)

        # скармливаем данные модели и вычисляем потери
        outputs = model(input_ids=input_ids, attention_mask=attention_mask, labels=labels, decoder_attention_mask=labels_attention_mask)
        loss = outputs.loss

        # обновляем отображение индикатора с текущими потерями
        batch_iterator.set_postfix(loss=loss.item())

        # Обратное распространение и обновление весов модели
        loss.backward()
        optimizer.step()
        optimizer.zero_grad()

    # Вывод информации о потерях и времени до окончания текущей эпохи
    time_remaining = (len(paraphrase_dataloader) - batch_iterator.n) * (time.time() - batch_iterator.start_t) / batch_iterator.n
    print(f"Epoch {epoch + 1}: Loss - {loss.item():.4f}, Time Remaining - {int(time_remaining // 60)}m {int(time_remaining % 60)}s")


#тут прописываем код к директории
save_path = "./model2/fine_tuned_paraphrase_model"

if not os.path.exists(save_path):
    os.makedirs(save_path)

model.save_pretrained(save_path)
tokenizer.save_pretrained(save_path)


/home/jupyter/.local/lib/python3.10/site-packages/transformers/optimization.py:429: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
Epoch 9:  67%|██████▋   | 1246/1849 [08:25<04:03,  2.47it/s, loss=0.158]